In [1]:
import json
import math
import queue as que

with open("Coord.json") as cord:
    coords = json.load(cord)
with open("Cost.json") as Cost:
    cost = json.load(Cost)
with open("Dist.json") as Dist:
    dist = json.load(Dist)
with open("G.json") as G:
    graph = json.load(G)

# Returns euclidean distance between the two nodes that are passed as arguments to this function
def euc_distance(node, connected_node):
    node_x, node_y = coords[node]
    connected_node_x, connected_node_y = coords[connected_node]
    return math.sqrt((node_x - connected_node_x) ** 2 + (node_y - connected_node_y) ** 2)

# This function manages a dictionary for all the visited nodes' paths
# If any node is visited then it's path is saved as an object in the dictionary, and this
# function will return the cost to reach that node along with the entire path

def append_to_path(path, node, parent):
    # Base case, if the node is empty then only one node is appended to the path and cost 0 is returned
    # as their is only one node in the path
    if len(path) == 0 and parent is None:
        return [node], 0

    # If the path already has one or more nodes in it, then the current node is appended into the parent's path
    # and the resulting path is allocated to the current node. The accumulated cost to reach the current node
    # is also returned
    path_to_return = []
    if parent in path:
        travel_cost = 0
        index = 0
        for path_node in path:
            # If we reach the parent node in path, then we append current node to it and the resulting path to the
            # current node is returned along with it's accumulated cost
            if path_node == parent:
                path_to_return.append(parent)
                travel_cost += cost[path[index]+","+node]
                path_to_return.append(node)
                return path_to_return, travel_cost
            path_to_return.append(path_node)
            travel_cost += cost[(path[index]+","+path[index + 1])]
            index += 1

# This function displays the path as specified in the requirements of any path_list that is passed to it as argument
def display_path(path_list):
    for i in range(len(path_list)):
        if i == len(path_list) - 1:
            print(path_list[i])
            break
        print(path_list[i]+"->", end="")

# Implementation of Greedy Best First Search for task1
def GBFS(start_node, goal_node):
    # PriorityQueue is maintained for sorting the accumulated cost for the current node
    priorityQueue = que.PriorityQueue()
    priorityQueue.put((0, start_node, None))
    visited_nodes = []
    # Total path is a dictionary that maintains the path_list for all the visited nodes
    total_path = {"1": ["1"]}
    total_cost = 0

    while not priorityQueue.empty():

        euc_dist, current_node, parent_node = priorityQueue.get()

        # In exception to the first iteration, the current node is appended to the path and resulting cost is
        # provided
        if parent_node is not None:
            path_list = total_path[parent_node]
            path_list, total_cost = append_to_path(path_list, current_node, parent_node)
            total_path[current_node] = path_list

        if current_node not in visited_nodes:
            visited_nodes.append(current_node)
            if current_node == goal_node:
                print("Shortest path: ", end="")
                display_path(total_path[current_node])
                print("Shortest distance: ", calculate_dist(total_path[current_node]))
                print("Total energy cost: ", calculate_cost(total_path[current_node]))
                return
            neighbors = graph[current_node]

            for neighbor in neighbors:
                # For GBFS, the approximate euc_dist to reach the goal_node from neighbor is stored in the priority
                # queue and thus based on shortest euc_dist, the algo works
                neighbor_euc_dist = euc_distance(neighbor, goal_node)
                priorityQueue.put((neighbor_euc_dist, neighbor, current_node))

# This function simply calculates the entire accumulated energy cost for any path list provided to it
def calculate_cost(path):
    path_cost = 0
    for index in range(len(path) - 1):
        path_cost += cost[(path[index] + "," + path[index + 1])]
    return path_cost

# This function simply calculates the entire accumulated distance for any path list provided to it
def calculate_dist(path):
    path_cost = 0
    for index in range(len(path) - 1):
        path_cost += dist[(path[index] + "," + path[index + 1])]
    return path_cost

# For task 2, implementation of Uniform Cost Search
def UCS(start_node, goal_node, energy_budget = 287932):
    # PriorityQueue is maintained for sorting the accumulated cost for the current node
    priorityQueue = que.PriorityQueue()
    priorityQueue.put((0, start_node, None))
    visited_nodes = []
    # Total path is a dictionary that maintains the path_list for all the visited nodes
    total_path = {"1": ["1"]}
    total_cost = 0

    while not priorityQueue.empty():
        travel_cost, current_node, parent_node = priorityQueue.get()

        # In exception to the first iteration, the current node is appended to the path and resulting cost is
        # provided
        if parent_node is not None:
            path_list = total_path[parent_node]
            path_list, total_cost = append_to_path(path_list, current_node, parent_node)
            total_path[current_node] = path_list

        visited_nodes.append(current_node)

        if current_node == goal_node:
            if calculate_cost(total_path[current_node]) > energy_budget:
                visited_nodes.remove(current_node)
            else:
                print("Shortest path: ", end="")
                display_path(total_path[current_node])
                print("Shortest distance: ", calculate_dist(total_path[current_node]))
                print("Total energy cost: ", calculate_cost(total_path[current_node]))
                return

        neighbors = graph[current_node]

        for neighbor in neighbors:
            # For UCS, the accumulated cost from start_node till neighbor node is stored in the priority
            # queue and thus based on shortest euc_dist, the algo works
            if neighbor not in visited_nodes or neighbor == goal_node:
                neighbor_dist = cost[current_node+","+neighbor]
                priorityQueue.put((neighbor_dist + travel_cost, neighbor, current_node))

def Astar(start_node, goal_node, energy_budget = 287932):
    # PriorityQueue is maintained for sorting the accumulated cost for the current node
    priorityQueue = que.PriorityQueue()
    priorityQueue.put((0, start_node, None))
    visited_nodes = []
    # Total path is a dictionary that maintains the path_list for all the visited nodes
    total_path = {"1": ["1"]}
    total_cost = 0

    while not priorityQueue.empty():

        travel_cost, current_node, parent_node = priorityQueue.get()
        dist_to_reach_current_node = 0

        # In exception to the first iteration, the current node is appended to the path and resulting cost is
        # provided
        if parent_node is not None:
            path_list = total_path[parent_node]
            path_list, dist_to_reach_current_node = append_to_path(path_list, current_node, parent_node)
            total_path[current_node] = path_list

        if current_node not in visited_nodes:
            visited_nodes.append(current_node)
            if current_node == goal_node:
                if calculate_cost(total_path[current_node]) > energy_budget:
                    visited_nodes.remove(current_node)
                else:
                    print("Shortest path: ", end="")
                    display_path(total_path[current_node])
                    print("Shortest distance: ", calculate_dist(total_path[current_node]))
                    print("Total energy cost: ", calculate_cost(total_path[current_node]))
                    return

            neighbors = graph[current_node]

            for neighbor in neighbors:
                # For Astar, the accumulated cost from start_node till neighbor node along with the estimated euc_dist
                # to reach the goal node from the neighbor is stored in the priority queue and thus based on shortest
                # euc_dist, the algo works
                neighbor_dist = cost[current_node+","+neighbor]
                dist_to_reach_neighbor = dist_to_reach_current_node + neighbor_dist
                euc_dist_to_goal_node = euc_distance(neighbor, goal_node)
                priorityQueue.put((dist_to_reach_neighbor + euc_dist_to_goal_node, neighbor, current_node))




if __name__ == '__main__':


    GBFS("1", "50")
    UCS("1", "50", 287932)
    Astar("1", "50", 287932)

Shortest path: 1->1363->1358->1357->1356->1276->1273->1277->1269->1241->1240->1235->956->953->955->947->944->948->949->952->1000->998->994->995->996->987->986->979->980->969->977->881->887->885->889->2365->2364->879->878->877->865->862->863->860->490->489->486->488->2019->2022->2000->1996->1998->1999->2005->2007->2009->2011->2059->2061->2062->2065->2057->2050->2051->1979->1975->1967->1966->1974->1973->1971->1970->1948->1937->1939->1935->1931->1934->1673->1675->1674->1837->1834->1829->1818->1816->1815->1634->1814->1755->1754->1753->1749->1752->1748->1746->1732->1695->1694->1701->1702->1699->5446->5444->5447->5439->5435->5433->5401->5400->5394->5291->5278->5289->5281->5269->5257->5268->50
Shortest distance:  204528.5096246559
Total energy cost:  438757
Shortest path: 1->1363->1358->1357->1356->1276->1273->1277->1269->1267->1242->1241->1240->1235->956->953->955->957->958->959->960->962->1002->952->1000->998->994->995->996->997->1011->6380->1020->1019->1323->2935->2936->2941->2942->2949->2

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



SyntaxError: invalid syntax (<ipython-input-82-e3dd41d8dae8>, line 13)

Reachable from A:
  Visiting 1
  Visiting 1363
  Visiting 12
  Visiting 2
  Visiting 1364
  Visiting 1358
  Visiting 13
  Visiting 48
  Visiting 1366
  Visiting 1365
  Visiting 1357
  Visiting 1355
  Visiting 1369
  Visiting 1367
  Visiting 1359
  Visiting 1356
  Visiting 1354
  Visiting 1274
  Visiting 1360
  Visiting 1403
  Visiting 1370
  Visiting 1368
  Visiting 1280
  Visiting 1276
  Visiting 1275
  Visiting 1183
  Visiting 1143
  Visiting 1362
  Visiting 1361
  Visiting 1401
  Visiting 1406
  Visiting 1407
  Visiting 1408
  Visiting 1388
  Visiting 1389
  Visiting 1278
  Visiting 1287
  Visiting 1273
  Visiting 1272
  Visiting 1181
  Visiting 1353
  Visiting 1264
  Visiting 1144
  Visiting 1218
  Visiting 1402
  Visiting 1417
  Visiting 6427
  Visiting 1391
  Visiting 1392
  Visiting 1425
  Visiting 1277
  Visiting 1279
  Visiting 1371
  Visiting 1288
  Visiting 1271
  Visiting 1220
  Visiting 1182
  Visiting 1239
  Visiting 1138
  Visiting 1136
  Visiting 1223
  Visiting 1216
  

  Visiting 4742
  Visiting 2326
  Visiting 4696
  Visiting 231
  Visiting 232
  Visiting 4596
  Visiting 4597
  Visiting 4591
  Visiting 283
  Visiting 280
  Visiting 270
  Visiting 6491
  Visiting 377
  Visiting 378
  Visiting 3985
  Visiting 4069
  Visiting 4070
  Visiting 3999
  Visiting 2680
  Visiting 2683
  Visiting 2873
  Visiting 2608
  Visiting 2612
  Visiting 2616
  Visiting 2623
  Visiting 2679
  Visiting 425
  Visiting 2666
  Visiting 424
  Visiting 3332
  Visiting 3324
  Visiting 3302
  Visiting 3307
  Visiting 3998
  Visiting 3997
  Visiting 2600
  Visiting 2601
  Visiting 2130
  Visiting 2148
  Visiting 2744
  Visiting 2702
  Visiting 2746
  Visiting 2272
  Visiting 2278
  Visiting 81
  Visiting 77
  Visiting 2150
  Visiting 2080
  Visiting 2065
  Visiting 2063
  Visiting 1991
  Visiting 1982
  Visiting 1889
  Visiting 1985
  Visiting 2002
  Visiting 1900
  Visiting 484
  Visiting 462
  Visiting 460
  Visiting 464
  Visiting 455
  Visiting 458
  Visiting 385
  Visiting 3

  Visiting 5493
  Visiting 5608
  Visiting 5631
  Visiting 5612
  Visiting 4379
  Visiting 4293
  Visiting 260849
  Visiting 4278
  Visiting 4284
  Visiting 4291
  Visiting 4329
  Visiting 4287
  Visiting 4260
  Visiting 4212
  Visiting 4214
  Visiting 257691
  Visiting 257646
  Visiting 261075
  Visiting 257730
  Visiting 257718
  Visiting 257782
  Visiting 257781
  Visiting 262372
  Visiting 257784
  Visiting 262994
  Visiting 257772
  Visiting 257796
  Visiting 257783
  Visiting 257786
  Visiting 260639
  Visiting 262010
  Visiting 260632
  Visiting 260631
  Visiting 260638
  Visiting 257752
  Visiting 257767
  Visiting 257764
  Visiting 264187
  Visiting 264186
  Visiting 260626
  Visiting 257753
  Visiting 246486
  Visiting 260628
  Visiting 259357
  Visiting 260079
  Visiting 260075
  Visiting 260087
  Visiting 260061
  Visiting 260058
  Visiting 260060
  Visiting 260323
  Visiting 260315
  Visiting 260108
  Visiting 260333
  Visiting 4952
  Visiting 260335
  Visiting 259879
  Vi

  Visiting 247486
  Visiting 247484
  Visiting 247886
  Visiting 247882
  Visiting 247496
  Visiting 247887
  Visiting 247499
  Visiting 258360
  Visiting 247906
  Visiting 247868
  Visiting 247867
  Visiting 247467
  Visiting 261358
  Visiting 247419
  Visiting 247429
  Visiting 247442
  Visiting 247391
  Visiting 247420
  Visiting 247390
  Visiting 244009
  Visiting 244018
  Visiting 244021
  Visiting 244253
  Visiting 244257
  Visiting 244230
  Visiting 244259
  Visiting 244264
  Visiting 244281
  Visiting 261553
  Visiting 244280
  Visiting 244288
  Visiting 244267
  Visiting 244242
  Visiting 244107
  Visiting 244232
  Visiting 261558
  Visiting 244246
  Visiting 244105
  Visiting 244099
  Visiting 244532
  Visiting 247376
  Visiting 247264
  Visiting 247262
  Visiting 247266
  Visiting 247267
  Visiting 247256
  Visiting 247258
  Visiting 247246
  Visiting 257614
  Visiting 247377
  Visiting 244528
  Visiting 244512
  Visiting 244521
  Visiting 243772
  Visiting 244490
  Visiting

  Visiting 243680
  Visiting 254898
  Visiting 240602
  Visiting 243335
  Visiting 243338
  Visiting 261947
  Visiting 243434
  Visiting 243437
  Visiting 243427
  Visiting 243430
  Visiting 243456
  Visiting 243448
  Visiting 243471
  Visiting 243468
  Visiting 243450
  Visiting 243444
  Visiting 243513
  Visiting 243481
  Visiting 243514
  Visiting 243520
  Visiting 257818
  Visiting 243314
  Visiting 243312
  Visiting 243316
  Visiting 243623
  Visiting 243610
  Visiting 243551
  Visiting 243537
  Visiting 243619
  Visiting 243535
  Visiting 243521
  Visiting 239122
  Visiting 244102
  Visiting 262805
  Visiting 262807
  Visiting 262834
  Visiting 261152
  Visiting 262833
  Visiting 238942
  Visiting 262863
  Visiting 257857
  Visiting 257854
  Visiting 257856
  Visiting 261148
  Visiting 262668
  Visiting 257956
  Visiting 257953
  Visiting 262079
  Visiting 257993
  Visiting 262087
  Visiting 255237
  Visiting 255235
  Visiting 262006
  Visiting 258691
  Visiting 255192
  Visiting

...

  Visiting 87460
  Visiting 87470
  Visiting 90830
  Visiting 87471
  Visiting 87468
  Visiting 87448
  Visiting 87457
  Visiting 87449
  Visiting 87451
  Visiting 88257
  Visiting 84312
  Visiting 84188
  Visiting 84234
  Visiting 90846
  Visiting 91132
  Visiting 84232
  Visiting 88821
  Visiting 90845
  Visiting 91131
  Visiting 89178
  Visiting 89187
  Visiting 89190
  Visiting 88780
  Visiting 88693
  Visiting 87763
  Visiting 88689
  Visiting 88705
  Visiting 90843
  Visiting 88787
  Visiting 88425
  Visiting 85210
  Visiting 91604
  Visiting 88917
  Visiting 91431
  Visiting 88390
  Visiting 91122
  Visiting 88431
  Visiting 88418
  Visiting 88285
  Visiting 88282
  Visiting 88428
  Visiting 90088
  Visiting 91797
  Visiting 91755
  Visiting 89062
  Visiting 80694
  Visiting 89977
  Visiting 89595
  Visiting 91172
  Visiting 89999
  Visiting 89529
  Visiting 89531
  Visiting 89997
  Visiting 91133
  Visiting 89482
  Visiting 89485
  Visiting 89494
  Visiting 89483
  Visiting 912

  Visiting 59398
  Visiting 59412
  Visiting 59414
  Visiting 59547
  Visiting 62749
  Visiting 62757
  Visiting 62751
  Visiting 62754
  Visiting 63536
  Visiting 63599
  Visiting 76475
  Visiting 66178
  Visiting 66193
  Visiting 66290
  Visiting 73192
  Visiting 66303
  Visiting 66310
  Visiting 73464
  Visiting 73477
  Visiting 63553
  Visiting 63551
  Visiting 63544
  Visiting 63543
  Visiting 60437
  Visiting 60441
  Visiting 77211
  Visiting 66213
  Visiting 66216
  Visiting 66215
  Visiting 66218
  Visiting 66211
  Visiting 65588
  Visiting 65600
  Visiting 66295
  Visiting 66192
  Visiting 66297
  Visiting 63547
  Visiting 63557
  Visiting 61810
  Visiting 61822
  Visiting 61805
  Visiting 61802
  Visiting 76647
  Visiting 61801
  Visiting 61751
  Visiting 61746
  Visiting 61736
  Visiting 61882
  Visiting 61899
  Visiting 77119
  Visiting 77117
  Visiting 61875
  Visiting 61849
  Visiting 61839
  Visiting 61731
  Visiting 61752
  Visiting 61755
  Visiting 61925
  Visiting 636

  Visiting 56876
  Visiting 61763
  Visiting 61778
  Visiting 58628
  Visiting 77516
  Visiting 77517
  Visiting 58202
  Visiting 58191
  Visiting 77532
  Visiting 58190
  Visiting 58321
  Visiting 58323
  Visiting 58276
  Visiting 58280
  Visiting 58274
  Visiting 58281
  Visiting 58897
  Visiting 59355
  Visiting 61781
  Visiting 61712
  Visiting 61766
  Visiting 61773
  Visiting 61688
  Visiting 61706
  Visiting 61548
  Visiting 61681
  Visiting 61546
  Visiting 61687
  Visiting 61560
  Visiting 61574
  Visiting 61565
  Visiting 61568
  Visiting 61570
  Visiting 61583
  Visiting 61582
  Visiting 61551
  Visiting 77828
  Visiting 63655
  Visiting 61633
  Visiting 61630
  Visiting 62008
  Visiting 61965
  Visiting 61616
  Visiting 61608
  Visiting 61612
  Visiting 61605
  Visiting 61644
  Visiting 61643
  Visiting 61666
  Visiting 61632
  Visiting 61631
  Visiting 61992
  Visiting 61963
  Visiting 61955
  Visiting 77537
  Visiting 61937
  Visiting 61957
  Visiting 61968
  Visiting 619

  Visiting 80102
  Visiting 91858
  Visiting 87522
  Visiting 91503
  Visiting 79992
  Visiting 79968
  Visiting 79994
  Visiting 79982
  Visiting 79967
  Visiting 80166
  Visiting 80096
  Visiting 80040
  Visiting 80118
  Visiting 80068
  Visiting 84859
  Visiting 57323
  Visiting 57385
  Visiting 57399
  Visiting 57390
  Visiting 78986
  Visiting 78985
  Visiting 57404
  Visiting 57407
  Visiting 57382
  Visiting 57376
  Visiting 56902
  Visiting 57397
  Visiting 57351
  Visiting 57403
  Visiting 57398
  Visiting 57367
  Visiting 57400
  Visiting 57372
  Visiting 57362
  Visiting 79106
  Visiting 79147
  Visiting 84866
  Visiting 84871
  Visiting 84840
  Visiting 84894
  Visiting 84895
  Visiting 79102
  Visiting 79101
  Visiting 79109
  Visiting 77984
  Visiting 77980
  Visiting 77976
  Visiting 77979
  Visiting 77986
  Visiting 79772
  Visiting 90915
  Visiting 90916
  Visiting 79761
  Visiting 79758
  Visiting 79259
  Visiting 79496
  Visiting 79498
  Visiting 79479
  Visiting 794

  Visiting 86614
  Visiting 86606
  Visiting 86060
  Visiting 86061
  Visiting 91081
  Visiting 81622
  Visiting 81623
  Visiting 90691
  Visiting 90692
  Visiting 81802
  Visiting 81843
  Visiting 90720
  Visiting 81950
  Visiting 81933
  Visiting 81930
  Visiting 81932
  Visiting 81876
  Visiting 81951
  Visiting 81959
  Visiting 81956
  Visiting 81943
  Visiting 83603
  Visiting 83335
  Visiting 83342
  Visiting 83376
  Visiting 83373
  Visiting 91007
  Visiting 83613
  Visiting 91009
  Visiting 83405
  Visiting 83370
  Visiting 83955
  Visiting 91842
  Visiting 91846
  Visiting 88717
  Visiting 83348
  Visiting 83451
  Visiting 83718
  Visiting 83484
  Visiting 83450
  Visiting 83478
  Visiting 83934
  Visiting 83933
  Visiting 85727
  Visiting 85612
  Visiting 85613
  Visiting 85719
  Visiting 85454
  Visiting 85467
  Visiting 85720
  Visiting 85714
  Visiting 85385
  Visiting 85372
  Visiting 83922
  Visiting 83920
  Visiting 85361
  Visiting 85362
  Visiting 85854
  Visiting 858

______________________________
 5  4  5  6  7  8  9  10 11 12
 4  3  4  5  10 13 10 11 12 13
 3  2  3  4  9  14 15 12 13 14
 2  1  2  3  8  13 .  17 Z  . 
 1  A  1  6  11 .  .  .  .  . 
 2  1  2  7  12 .  .  .  .  . 
 3  2  3  4  9  .  .  .  .  . 
 4 ######### .  .  .  .  .  . 
 . ######### .  .  .  .  .  . 
 .  .  .  .  .  .  .  .  .  . 
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~


__________________________________________________________________________________________
 >  >  >  v  v  v  v  v  v  v  v  v  v  v  v  v  <  <  <  <  < ###### v  v  v  v  v  v  v 
 >  >  >  >  v  v  v  v  v  v  v  v  v  v  v  <  <  <  <  <  < ###### >  v  v  v  v  v  v 
 >  >  >  >  >  v  v  v  v  v  v  v  v  v  <  <  <  <  <  <  < ###### >  >  v  v  v  v  v 
 >  >  ^ ###### v  v  v  v  v  v  v  v  <  <  <  <  <  <  <  < ###### >  >  >  v  v  v  v 
 >  ^  ^ ###### v  v  v  v  v  v  v  < ###### ^  <  <  <  <  < ###### >  >  >  v  v  v  v 
 ^  ^  ^ ###### >  v  v  v  v  v  <  < ###### ^  ^  <  <  <  < ############### v  v  v  < 
 ^  ^  ^ ###### >  >  v  v  v  <  <  < ###### ^  ^  ^  <  <  < ############### v  v  <  < 
 v  v  v ###### >  >  >  A  <  <  <  < ###### ^  ^  ^  ^  <  <  <  <  <  <  <  <  <  <  < 
 v  v  v ###### >  >  ^  ^  ^  <  <  < ###### ^  ^  ^  ^  ^  <  <  <  <  <  <  <  <  <  < 
 v  v  v ###### >  ^  ^  ^  ^  ^  <  < ###### ^  ^  ^  ^  ^  ^  <  <  <  <  <  <  <  <  < 

In [14]:

draw_grid(g, point_to=parents, start=start, goal=goal)

__________________________________________________________________________________________
 .  >  >  v  v  v  v  v  v  v  v  v  v  v  v  v  <  .  .  .  . ###### .  .  .  .  .  .  . 
 >  >  >  >  v  v  v  v  v  v  v  v  v  v  v  <  <  <  .  .  . ###### .  .  .  .  .  .  . 
 >  >  >  >  >  v  v  v  v  v  v  v  v  v  <  <  <  Z  .  .  . ###### .  .  .  .  .  .  . 
 >  >  ^ ###### v  v  v  v  v  v  v  v  <  <  <  <  <  <  .  . ###### .  .  .  .  .  .  . 
 .  ^  ^ ###### v  v  v  v  v  v  v  < ###### ^  <  <  .  .  . ###### .  .  .  .  .  .  . 
 .  .  ^ ###### >  v  v  v  v  v  <  < ###### ^  ^  .  .  .  . ############### .  .  .  . 
 .  .  . ###### >  >  v  v  v  <  <  < ###### ^  .  .  .  .  . ############### .  .  .  . 
 .  .  . ###### >  >  >  A  <  <  <  < ###### .  .  .  .  .  .  .  .  .  .  .  .  .  .  . 
 .  .  . ###### >  >  ^  ^  ^  <  <  < ###### .  .  .  .  .  .  .  .  .  .  .  .  .  .  . 
 .  .  v ###### >  ^  ^  ^  ^  ^  <  < ###### .  .  .  .  .  .  .  .  .  .  .  .  .  .  . 

AttributeError: 'dict' object has no attribute 'is_multigraph'

In [90]:
#graph first 50
g =    {"1": ["1363", "12", "2"],
     "2": ["13", "1", "48"],
     "3": ["4", "3874"],
     "4": ["3926", "3", "3937"],
     "5": ["6", "1204", "1214", "1219"],
     "6": ["5"],
     "7": ["1147", "8", "1148"],
     "8": ["7"],
     "9": ["11", "603", "10"],
     "10": ["6444", "9", "1197"],
     "11": ["9"],
     "12": ["1"],
     "13": ["2"],
     "14": ["237", "251", "15"],
     "15": ["14"],
     "16": ["4151", "17"], 
     "17": ["16", "4446"],
     "18": ["19", "4266", "6362"],
     "19": ["18"],
     "20": ["4321", "21", "22"],
     "21": ["20", "4315", "4323"],
     "22": ["20"],
     "23": ["24", "6095", "6086"],
     "24": ["23"],
     "25": ["4972", "4099", "26"],
     "26": ["5001", "25", "4999"],
     "27": ["28", "2494"],
     "28": ["2494", "27"],
     "29": ["42", "30", "1150"],
     "30": ["1152", "29"],
     "31": ["32", "39"],
     "32": ["31"],
     "33": ["34", "1730", "35"], 
     "34": ["33", "230"],
     "35": ["33", "249"],
     "36": ["4917", "37"],
     "37": ["36"],
     "38": ["39", "4691"],
     "39": ["38", "31", "4681"],
     "40": ["41", "4857"], "41": ["40", "4855", "4858"],
     "42": ["29"], "43": ["44", "5063", "5065"],
     "44": ["43", "45"], "45": ["44", "260442"], 
     "46": ["4497", "47"], "47": ["260314", "4928", "46"],
     "48": ["2"], "49": ["50", "51", "5261"], 
     "50": ["5268", "5280", "49"], }

SyntaxError: invalid syntax (<ipython-input-96-8de183043a63>, line 3)

In [ ]:
#distance first 50

{"1,2": 803, "2,1": 803, 
 "3,4": 158, "4,3": 158,
 "5,6": 923.7819006670352, "6,5": 923.7819006670352,
 "7,8": 1825.4232385942719, "8,7": 1825.4232385942719,
 "9,10": 1673, "10,9": 1673,
 "9,11": 1501.6324450410627, "11,9": 1501.6324450410627, 
 "1,12": 1004.7188661511238, "12,1": 1004.7188661511238,
 "2,13": 704.9198536003934, "13,2": 704.9198536003934,
 "14,15": 1635.6191488240775, "15,14": 1635.6191488240775,
 "16,17": 1670.4613135298885, "17,16": 1670.4613135298885, 
 "18,19": 1012, "19,18": 1012, "20,21": 1226, "21,20": 1226, 
 "20,22": 1513.8097634775645, "22,20": 1513.8097634775645, 
 "23,24": 2707, "24,23": 2707, "25,26": 595.5845867716861,
 "26,25": 595.5845867716861, "27,28": 783, "28,27": 783,
 
 "29,30": 617.5694292952007, "30,29": 617.5694292952007,
 "31,32": 3909.646659226381, "32,31": 3909.646659226381, 
 "33,34": 1994, "34,33": 1994, "33,35": 397.39401102683973, 
 "35,33": 397.39401102683973, "36,37": 363, "37,36": 363, 
 "38,39": 1018, "39,38": 1018, "40,41": 392, "41,40": 392, 
 "29,42": 1074, "42,29": 1074, "43,44": 570, "44,43": 570, 
 "44,45": 1764, "45,44": 1764, "46,47": 1104, "47,46": 1104,
 "2,48": 617, "48,2": 617, "49,50": 1515, "50,49": 1515 }

In [ ]:
#cost first 50

{"1,2": 2008,"2,1": 2008, 
 "3,4": 395, "4,3": 395, 
 "5,6": 1935, "6,5": 1935, 
 "7,8": 3828, "8,7": 3828,
 "9,10": 4182, "10,9": 4182, 
 "9,11": 3500, "11,9": 3500, 
 "1,12": 2105, "12,1": 2105, 
 "2,13": 1478, "13,2": 1478, 
 "14,15": 3427, "15,14": 3427,
 "16,17": 4148, "17,16": 4148,
 "18,19": 2529, "19,18": 2529,
 "20,21": 3065, "21,20": 3065, 
 "20,22": 3163, "22,20": 3163, 
 "23,24": 6768, "24,23": 6768, 
 "25,26": 1300, "26,25": 1300,
 "27,28": 1957, "28,27": 1957,
 "29,30": 1295, "30,29": 1295,
 "31,32": 8530, "32,31": 8530,
 "33,34": 4986, "34,33": 4986, 
 "33,35": 843, "35,33": 843, 
 "36,37": 908, "37,36": 908, 
 "38,39": 2545, "39,38": 2545,
 "40,41": 980, "41,40": 980,
 "29,42": 2686, "42,29": 2686,
 "43,44": 1425, "44,43": 1425,
 "44,45": 4410, "45,44": 4410,
 "46,47": 2759, "47,46": 2759,
 "2,48": 1541, "48,2": 1541, 
 "49,50": 3787, "50,49": 3787, 